<a href="https://colab.research.google.com/github/rgw3wgs/CS2-DS4002/blob/main/ETL_Data_Processor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Travel Booking Site to India

In [1]:
import sqlite3
import requests
import random
import csv

In [2]:
import sqlite3


def create_tables():
    conn = sqlite3.connect('travel_booking.db')
    cursor = conn.cursor()

    #Customers table
    cursor.execute('''
        CREATE TABLE IF NOT EXISTS customers (
            customer_id INTEGER PRIMARY KEY,
            name TEXT NOT NULL
        )
    ''')

    #Bookings table
    cursor.execute('''
        CREATE TABLE IF NOT EXISTS bookings (
            booking_id INTEGER PRIMARY KEY,
            customer_id INTEGER NOT NULL,
            destination TEXT NOT NULL,
            arrival_time TEXT NOT NULL,
            FOREIGN KEY (customer_id) REFERENCES customers(customer_id)
        )
    ''')

    #Flights table
    cursor.execute('''
        CREATE TABLE IF NOT EXISTS flights (
            airline TEXT NOT NULL,
            flight TEXT NOT NULL,
            source_city TEXT NOT NULL,
            departure_time TEXT NOT NULL,
            stops TEXT NOT NULL,
            arrival_time TEXT NOT NULL,
            destination_city TEXT NOT NULL,
            flight_class TEXT NOT NULL,
            duration INTEGER NOT NULL,
            days_left INTEGER NOT NULL,
            price REAL NOT NULL
        )
    ''')

    #Weather table
    cursor.execute('''
        CREATE TABLE IF NOT EXISTS weather (
            city TEXT PRIMARY KEY,
            temperature REAL NOT NULL,
            humidity INTEGER NOT NULL,
            weather_description TEXT NOT NULL
        )
    ''')
    conn.commit()
    conn.close()



create_tables()

In [3]:
api_key = "b9adf9aff2c0357f2c3f9d15857307e0"

In [4]:

# Function to fetch weather data from OpenWeather API
def getWeather(api_key, city):
      url = f'http://api.openweathermap.org/data/2.5/weather?q={city}&appid={api_key}&units=metric'
      response = requests.get(url)
      response.raise_for_status()
      data = response.json()

        # weather from API
      temperature = data['main']['temp']
      humidity = data['main']['humidity']
      weather_description = data['weather'][0]['description']

      return temperature, humidity, weather_description



In [5]:
# example call
getWeather(api_key, 'Mumbai')

(30.99, 70, 'haze')

In [6]:
# transferring customer data into a table
def customer_data(filename):
    conn = sqlite3.connect('travel_booking.db')
    cursor = conn.cursor()

    try:
        with open(filename, 'r') as file:
            reader = csv.reader(file)
            next(reader)
            for row in reader:
                cursor.execute('''
                    INSERT INTO customers (customer_id, name)
                    VALUES (?, ?)
                ''', (row[0], row[1]))


        conn.commit()
        print("Customer data loaded successfully.")
    except Exception as e:
        print("Error loading customer data:", e)
    finally:

        conn.close()


In [7]:
customer_data('Names.csv')

Customer data loaded successfully.


In [8]:
#turning booking csv into a table
def booking_data(filename):
    conn = sqlite3.connect('travel_booking.db')
    cursor = conn.cursor()

    try:
        with open(filename, 'r') as file:
            reader = csv.reader(file)
            next(reader)
            for row in reader:
                booking_id, customer_id, destination, arrival_time= row

                cursor.execute('''
                    INSERT INTO bookings (booking_id, customer_id, destination, arrival_time)
                    VALUES (?, ?, ?, ?)
                ''', (booking_id, customer_id, destination, arrival_time))


        conn.commit()
        print("Booking data loaded successfully.")
    except Exception as e:
        print("Error loading booking data:", e)
    finally:
        conn.close()

In [9]:
booking_data('Booking.csv')

Booking data loaded successfully.


In [10]:
#turning flight data into a table
def flight_data(filename):
    column_mapping = {
        'class': 'flight_class'
    }

    conn = sqlite3.connect('travel_booking.db')
    cursor = conn.cursor()

    try:
        with open(filename, 'r') as file:
            reader = csv.DictReader(file)
            for row in reader:
                airline = row['airline']
                flight = row['flight']
                source_city = row['source_city']
                departure_time = row['departure_time']
                stops = row['stops']
                arrival_time = row['arrival_time']
                destination_city = row['destination_city']
                flight_class = row['class']
                duration = row['duration']
                days_left = row['days_left']
                price = row['price']

                # Insert flight data into Flights table
                cursor.execute('''
                    INSERT INTO flights (airline, flight, source_city, departure_time, stops, arrival_time, destination_city, flight_class, duration, days_left, price)
                    VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
                ''', (airline, flight, source_city, departure_time, stops, arrival_time, destination_city, flight_class, duration, days_left, price))

        conn.commit()
        print("Flight data loaded successfully.")
    except Exception as e:
        print("Error loading flight data:", e)
    finally:
        conn.close()




In [11]:
flight_data('Clean_Dataset.csv')

Flight data loaded successfully.


In [12]:
#load customers
conn = sqlite3.connect('travel_booking.db')

cursor = conn.cursor()
cursor.execute("SELECT * FROM customers")
rows = cursor.fetchall()
for row in rows:
    print(row)



(1, 'Rebekah')
(2, 'Nina')
(3, 'Michelle')
(4, 'Meek')
(5, 'Ahellah')
(6, 'Rachel')
(7, 'Emera')
(8, 'Noah')
(9, 'Daniel')
(10, 'Grace')
(11, 'Lawrence')
(12, 'Weaver')
(13, 'Katie')
(14, 'Alexis')
(15, 'John')
(16, 'Joseph')
(17, 'Brandon')
(18, 'Mariah')
(19, 'Stephanie')
(20, 'Mackenzie')
(21, 'Jerry')
(22, 'Chris')
(23, 'Rana')
(24, 'Princess')
(25, 'Jessica')
(26, 'Robert')
(27, 'Lex')
(28, 'Taylor')
(29, 'Nicole')
(30, 'Ben')


In [13]:
#load bookings table
cursor = conn.cursor()
cursor.execute("SELECT * FROM bookings")
rows = cursor.fetchall()
for row in rows:
    print(row)


(1, 1, 'Mumbai', 'Early_Morning')
(2, 2, 'Bangalore', 'Early_Morning')
(3, 3, 'Kolkata', 'Early_Morning')
(4, 4, 'Hyderabad', 'Early_Morning')
(5, 5, 'Chennai', 'Early_Morning')
(6, 6, 'Delhi', 'Early_Morning')
(7, 7, 'Mumbai', 'Night')
(8, 8, 'Bangalore', 'Night')
(9, 9, 'Kolkata', 'Night')
(10, 10, 'Hyderabad', 'Night')
(11, 11, 'Chennai', 'Night')
(12, 12, 'Delhi', 'Night')
(13, 13, 'Mumbai', 'Evening')
(14, 14, 'Bangalore', 'Evening')
(15, 15, 'Kolkata', 'Evening')
(16, 16, 'Hyderabad', 'Evening')
(17, 17, 'Chennai', 'Evening')
(18, 18, 'Delhi', 'Evening')
(19, 19, 'Mumbai', 'Afternoon')
(20, 20, 'Bangalore', 'Afternoon')
(21, 21, 'Kolkata', 'Afternoon')
(22, 22, 'Hyderabad', 'Afternoon')
(23, 23, 'Chennai', 'Afternoon')
(24, 24, 'Delhi', 'Afternoon')
(25, 25, 'Mumbai', 'Morning')
(26, 26, 'Bangalore', 'Morning')
(27, 27, 'Kolkata', 'Morning')
(28, 28, 'Hyderabad', 'Morning')
(29, 29, 'Chennai', 'Morning')
(30, 30, 'Delhi', 'Morning')


In [14]:
# load weather table
cursor = conn.cursor()
cursor.execute("SELECT * FROM weather")
rows = cursor.fetchall()
for row in rows:
    print(row)


In [15]:
cursor = conn.cursor()
cursor.execute("SELECT * FROM flights")
rows = cursor.fetchall()
for row in rows:
    print(row)

Streaming output truncated to the last 5000 lines.
('Vistara', 'UK-975', 'Delhi', 'Early_Morning', 'one', 'Evening', 'Kolkata', 'Economy', 11.08, 16, 7910.0)
('Vistara', 'UK-975', 'Delhi', 'Early_Morning', 'one', 'Evening', 'Kolkata', 'Economy', 14.17, 16, 7910.0)
('Vistara', 'UK-981', 'Delhi', 'Night', 'one', 'Evening', 'Kolkata', 'Economy', 19, 16, 7910.0)
('Vistara', 'UK-953', 'Delhi', 'Night', 'one', 'Evening', 'Kolkata', 'Economy', 20.17, 16, 7910.0)
('Indigo', '6E-397', 'Delhi', 'Afternoon', 'one', 'Evening', 'Kolkata', 'Economy', 5.25, 16, 7602.0)
('Vistara', 'UK-951', 'Delhi', 'Afternoon', 'one', 'Evening', 'Kolkata', 'Economy', 5.58, 16, 8134.0)
('Vistara', 'UK-995', 'Delhi', 'Morning', 'one', 'Evening', 'Kolkata', 'Economy', 6.5, 16, 8134.0)
('Vistara', 'UK-993', 'Delhi', 'Afternoon', 'one', 'Evening', 'Kolkata', 'Economy', 7.08, 16, 8134.0)
('Vistara', 'UK-927', 'Delhi', 'Morning', 'one', 'Evening', 'Kolkata', 'Economy', 7.33, 16, 8134.0)
('Vistara', 'UK-945', 'Delhi', 'Morn

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('Air_India', 'AI-651', 'Mumbai', 'Morning', 'one', 'Morning', 'Delhi', 'Economy', 25.08, 29, 5840.0)
('GO_FIRST', 'G8-349', 'Mumbai', 'Morning', 'one', 'Evening', 'Delhi', 'Economy', 7.5, 29, 5912.0)
('Air_India', 'AI-673', 'Mumbai', 'Early_Morning', 'one', 'Afternoon', 'Delhi', 'Economy', 6.75, 29, 5915.0)
('Air_India', 'AI-673', 'Mumbai', 'Early_Morning', 'one', 'Night', 'Delhi', 'Economy', 13, 29, 5915.0)
('GO_FIRST', 'G8-7546', 'Mumbai', 'Evening', 'one', 'Late_Night', 'Delhi', 'Economy', 6.83, 29, 5942.0)
('GO_FIRST', 'G8-287', 'Mumbai', 'Morning', 'one', 'Evening', 'Delhi', 'Economy', 6.92, 29, 5942.0)
('GO_FIRST', 'G8-7545', 'Mumbai', 'Afternoon', 'two_or_more', 'Night', 'Delhi', 'Economy', 9.33, 29, 5942.0)
('GO_FIRST', 'G8-287', 'Mumbai', 'Morning', 'one', 'Night', 'Delhi', 'Economy', 9.67, 29, 5942.0)
('GO_FIRST', 'G8-371', 'Mumbai', 'Evening', 'one', 'Late_Night', 'Delhi', 'Economy', 9.83, 29, 5942.0)
('GO_FIRST', 'G8-383',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('Indigo', '6E-6257', 'Bangalore', 'Early_Morning', 'one', 'Afternoon', 'Delhi', 'Economy', 6, 47, 3245.0)
('Indigo', '6E-6067', 'Bangalore', 'Evening', 'one', 'Night', 'Delhi', 'Economy', 6.25, 47, 3245.0)
('Indigo', '6E-6491', 'Bangalore', 'Afternoon', 'one', 'Night', 'Delhi', 'Economy', 7.25, 47, 3245.0)
('Indigo', '6E-6178', 'Bangalore', 'Night', 'one', 'Early_Morning', 'Delhi', 'Economy', 7.5, 47, 3245.0)
('Indigo', '6E-6067', 'Bangalore', 'Evening', 'one', 'Late_Night', 'Delhi', 'Economy', 7.75, 47, 3245.0)
('Indigo', '6E-6067', 'Bangalore', 'Evening', 'one', 'Late_Night', 'Delhi', 'Economy', 8.5, 47, 3245.0)
('Indigo', '6E-684', 'Bangalore', 'Night', 'one', 'Early_Morning', 'Delhi', 'Economy', 9.33, 47, 3245.0)
('GO_FIRST', 'G8-294', 'Bangalore', 'Evening', 'one', 'Late_Night', 'Delhi', 'Economy', 4.92, 47, 3319.0)
('Vistara', 'UK-897', 'Bangalore', 'Early_Morning', 'one', 'Afternoon', 'Delhi', 'Economy', 4.58, 47, 3811.0)
('GO_

...

Streaming output truncated to the last 5000 lines.
('Air_India', 'AI-402', 'Kolkata', 'Morning', 'one', 'Night', 'Hyderabad', 'Business', 10.17, 27, 52063.0)
('Air_India', 'AI-763', 'Kolkata', 'Early_Morning', 'one', 'Evening', 'Hyderabad', 'Business', 12.33, 27, 52063.0)
('Air_India', 'AI-402', 'Kolkata', 'Morning', 'one', 'Night', 'Hyderabad', 'Business', 13.17, 27, 52063.0)
('Air_India', 'AI-763', 'Kolkata', 'Early_Morning', 'one', 'Night', 'Hyderabad', 'Business', 13.58, 27, 52063.0)
('Air_India', 'AI-770', 'Kolkata', 'Night', 'one', 'Morning', 'Hyderabad', 'Business', 14, 27, 52063.0)
('Air_India', 'AI-770', 'Kolkata', 'Night', 'one', 'Morning', 'Hyderabad', 'Business', 15.42, 27, 52063.0)
('Air_India', 'AI-763', 'Kolkata', 'Early_Morning', 'one', 'Night', 'Hyderabad', 'Business', 16.58, 27, 52063.0)
('Air_India', 'AI-424', 'Kolkata', 'Afternoon', 'one', 'Morning', 'Hyderabad', 'Business', 21, 27, 52063.0)
('Air_India', 'AI-424', 'Kolkata', 'Afternoon', 'one', 'Morning', 'Hyderaba

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('Air_India', 'AI-543', 'Hyderabad', 'Morning', 'one', 'Morning', 'Chennai', 'Business', 21.58, 31, 51595.0)
('Air_India', 'AI-840', 'Hyderabad', 'Night', 'one', 'Evening', 'Chennai', 'Business', 22.17, 31, 51595.0)
('Air_India', 'AI-543', 'Hyderabad', 'Morning', 'one', 'Afternoon', 'Chennai', 'Business', 25.33, 31, 51595.0)
('Air_India', 'AI-559', 'Hyderabad', 'Early_Morning', 'one', 'Morning', 'Chennai', 'Business', 26.42, 31, 51595.0)
('Vistara', 'UK-880', 'Hyderabad', 'Afternoon', 'one', 'Night', 'Chennai', 'Business', 6.83, 31, 58282.0)
('Vistara', 'UK-880', 'Hyderabad', 'Afternoon', 'one', 'Night', 'Chennai', 'Business', 9.33, 31, 58282.0)
('Vistara', 'UK-890', 'Hyderabad', 'Evening', 'one', 'Morning', 'Chennai', 'Business', 16.25, 31, 58282.0)
('Vistara', 'UK-880', 'Hyderabad', 'Afternoon', 'one', 'Morning', 'Chennai', 'Business', 20.5, 31, 58282.0)
('Vistara', 'UK-890', 'Hyderabad', 'Evening', 'one', 'Evening', 'Chennai', 'Busi

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



('Vistara', 'UK-822', 'Chennai', 'Morning', 'one', 'Afternoon', 'Hyderabad', 'Business', 26.5, 36, 41064.0)
('Vistara', 'UK-836', 'Chennai', 'Morning', 'one', 'Evening', 'Hyderabad', 'Business', 6.25, 36, 51457.0)
('Vistara', 'UK-836', 'Chennai', 'Morning', 'one', 'Evening', 'Hyderabad', 'Business', 9.17, 36, 51457.0)
('Vistara', 'UK-832', 'Chennai', 'Early_Morning', 'one', 'Evening', 'Hyderabad', 'Business', 10.08, 36, 51457.0)
('Vistara', 'UK-836', 'Chennai', 'Morning', 'one', 'Night', 'Hyderabad', 'Business', 12.17, 36, 51457.0)
('Vistara', 'UK-838', 'Chennai', 'Night', 'one', 'Morning', 'Hyderabad', 'Business', 12.58, 36, 51457.0)
('Vistara', 'UK-832', 'Chennai', 'Early_Morning', 'one', 'Evening', 'Hyderabad', 'Business', 13, 36, 51457.0)
('Vistara', 'UK-838', 'Chennai', 'Night', 'one', 'Afternoon', 'Hyderabad', 'Business', 15.5, 36, 51457.0)
('Vistara', 'UK-832', 'Chennai', 'Early_Morning', 'one', 'Night', 'Hyderabad', 'Business', 16, 36, 51457.0)
('Vistara', 'UK-834', 'Chennai', 

In [18]:

def flight_weather():
    try:
        conn = sqlite3.connect('travel_booking.db')
        cursor = conn.cursor()

        # Create a new table 'flight_weather' \
        cursor.execute('''
            CREATE TABLE IF NOT EXISTS flight_weather (
                destination_city TEXT PRIMARY KEY,
                temperature REAL,
                humidity INTEGER,
                weather_description TEXT
            )
        ''')

        # destination cities from the flights table
        cursor.execute('SELECT DISTINCT destination_city FROM flights')
        cities = cursor.fetchall()

        # get weather data for each destination city and insert into the 'flight_weather' table
        for city in cities:
            city = city[0]
            temperature, humidity, weather_description = getWeather(api_key, city)

            cursor.execute('''
                    INSERT OR REPLACE INTO flight_weather (destination_city, temperature, humidity, weather_description)
                    VALUES (?, ?, ?, ?)
                ''', (city, temperature, humidity, weather_description))

        # Commit changes and close connection
        conn.commit()
        print("Flight weather data loaded successfully.")
    except sqlite3.Error as e:
        print("Error creating flight_weather table:", e)
    finally:
        if conn:
          conn.close()

In [19]:
flight_weather()

Flight weather data loaded successfully.


In [20]:
# combine weather with name of cities from database
conn = sqlite3.connect('travel_booking.db')
cursor = conn.cursor()
cursor.execute("SELECT * FROM flight_weather")
rows = cursor.fetchall()
for row in rows:
    print(row)

('Mumbai', 30.99, 66, 'haze')
('Bangalore', 29.22, 56, 'scattered clouds')
('Kolkata', 31.97, 74, 'haze')
('Hyderabad', 30.23, 66, 'few clouds')
('Chennai', 33.37, 70, 'scattered clouds')
('Delhi', 31.05, 42, 'haze')


In [21]:
#Drop a few variables from flights table
try:
    conn = sqlite3.connect('travel_booking.db')
    cursor = conn.cursor()

    # new table
    cursor.execute('''
        CREATE TABLE flights_temp AS
        SELECT airline, source_city, departure_time, stops, arrival_time, destination_city, price
        FROM flights
    ''')

    # Drop the original flights table
    cursor.execute('DROP TABLE flights')

    # Rename the new table to flights
    cursor.execute('ALTER TABLE flights_temp RENAME TO flights')

    print("Columns removed successfully from the flights table.")
except sqlite3.Error as e:
    print("Error removing columns from the flights table:", e)
finally:
    if conn:
        conn.close()

Columns removed successfully from the flights table.


In [22]:
#load flights table
conn = sqlite3.connect('travel_booking.db')
cursor = conn.cursor()
cursor.execute("SELECT * FROM flights")
rows = cursor.fetchall()
for row in rows:
    print(row)

Streaming output truncated to the last 5000 lines.
('Air_India', 'Delhi', 'Morning', 'one', 'Night', 'Hyderabad', 5950.0)
('Air_India', 'Delhi', 'Night', 'one', 'Evening', 'Hyderabad', 5950.0)
('Air_India', 'Delhi', 'Night', 'one', 'Night', 'Hyderabad', 5950.0)
('Air_India', 'Delhi', 'Evening', 'one', 'Evening', 'Hyderabad', 5950.0)
('Air_India', 'Delhi', 'Evening', 'one', 'Night', 'Hyderabad', 5950.0)
('Air_India', 'Delhi', 'Morning', 'one', 'Afternoon', 'Hyderabad', 5955.0)
('Air_India', 'Delhi', 'Early_Morning', 'one', 'Evening', 'Hyderabad', 5989.0)
('Air_India', 'Delhi', 'Evening', 'one', 'Evening', 'Hyderabad', 5989.0)
('GO_FIRST', 'Delhi', 'Early_Morning', 'one', 'Afternoon', 'Hyderabad', 6109.0)
('Indigo', 'Delhi', 'Early_Morning', 'one', 'Afternoon', 'Hyderabad', 6227.0)
('Air_India', 'Delhi', 'Night', 'one', 'Night', 'Hyderabad', 6569.0)
('Indigo', 'Delhi', 'Early_Morning', 'one', 'Morning', 'Hyderabad', 6594.0)
('Indigo', 'Delhi', 'Afternoon', 'one', 'Evening', 'Hyderabad', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('GO_FIRST', 'Hyderabad', 'Afternoon', 'one', 'Night', 'Mumbai', 5420.0)
('GO_FIRST', 'Hyderabad', 'Early_Morning', 'one', 'Evening', 'Mumbai', 5420.0)
('GO_FIRST', 'Hyderabad', 'Early_Morning', 'one', 'Afternoon', 'Mumbai', 5529.0)
('GO_FIRST', 'Hyderabad', 'Early_Morning', 'one', 'Night', 'Mumbai', 5529.0)
('Indigo', 'Hyderabad', 'Afternoon', 'one', 'Evening', 'Mumbai', 5604.0)
('Air_India', 'Hyderabad', 'Early_Morning', 'one', 'Evening', 'Mumbai', 5815.0)
('Air_India', 'Hyderabad', 'Early_Morning', 'one', 'Evening', 'Mumbai', 5815.0)
('Vistara', 'Hyderabad', 'Afternoon', 'one', 'Night', 'Mumbai', 6191.0)
('GO_FIRST', 'Hyderabad', 'Morning', 'one', 'Night', 'Mumbai', 5865.0)
('Vistara', 'Hyderabad', 'Morning', 'one', 'Night', 'Mumbai', 6341.0)
('Vistara', 'Hyderabad', 'Early_Morning', 'one', 'Night', 'Mumbai', 6341.0)
('Air_India', 'Hyderabad', 'Morning', 'one', 'Evening', 'Mumbai', 6167.0)
('Vistara', 'Hyderabad', 'Morning', 'one', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('Vistara', 'Mumbai', 'Evening', 'one', 'Afternoon', 'Delhi', 41269.0)
('Vistara', 'Mumbai', 'Morning', 'one', 'Morning', 'Delhi', 41269.0)
('Vistara', 'Mumbai', 'Morning', 'one', 'Afternoon', 'Delhi', 41269.0)
('Vistara', 'Mumbai', 'Early_Morning', 'one', 'Morning', 'Delhi', 41269.0)
('Vistara', 'Mumbai', 'Evening', 'one', 'Night', 'Delhi', 41269.0)
('Air_India', 'Mumbai', 'Early_Morning', 'one', 'Afternoon', 'Delhi', 41101.0)
('Air_India', 'Mumbai', 'Early_Morning', 'one', 'Evening', 'Delhi', 41101.0)
('Air_India', 'Mumbai', 'Early_Morning', 'one', 'Morning', 'Delhi', 41101.0)
('Vistara', 'Mumbai', 'Morning', 'zero', 'Afternoon', 'Delhi', 42412.0)
('Vistara', 'Mumbai', 'Afternoon', 'one', 'Evening', 'Delhi', 44069.0)
('Vistara', 'Mumbai', 'Afternoon', 'one', 'Evening', 'Delhi', 44069.0)
('Air_India', 'Mumbai', 'Morning', 'one', 'Afternoon', 'Delhi', 44013.0)
('Vistara', 'Mumbai', 'Evening', 'zero', 'Night', 'Delhi', 44652.0)
('Vistar

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
('Vistara', 'Chennai', 'Night', 'one', 'Evening', 'Bangalore', 44144.0)
('Vistara', 'Chennai', 'Morning', 'one', 'Early_Morning', 'Bangalore', 44144.0)
('Vistara', 'Chennai', 'Afternoon', 'one', 'Morning', 'Bangalore', 44144.0)
('Vistara', 'Chennai', 'Night', 'one', 'Evening', 'Bangalore', 44144.0)
('Vistara', 'Chennai', 'Morning', 'one', 'Morning', 'Bangalore', 44144.0)
('Air_India', 'Chennai', 'Morning', 'one', 'Late_Night', 'Bangalore', 44546.0)
('Air_India', 'Chennai', 'Afternoon', 'two_or_more', 'Evening', 'Bangalore', 51928.0)
('Vistara', 'Chennai', 'Evening', 'one', 'Night', 'Bangalore', 60260.0)
('Vistara', 'Chennai', 'Morning', 'one', 'Evening', 'Bangalore', 60260.0)
('Vistara', 'Chennai', 'Morning', 'one', 'Evening', 'Bangalore', 60260.0)
('Vistara', 'Chennai', 'Morning', 'one', 'Night', 'Bangalore', 60260.0)
('Vistara', 'Chennai', 'Early_Morning', 'one', 'Evening', 'Bangalore', 60260.0)
('Vistara', 'Chennai', 'Early_Morning'

In [25]:
conn = sqlite3.connect('travel_booking.db')
cursor = conn.cursor()

#grouping number of people by destination
sql_query = """
SELECT destination, COUNT(*)
FROM bookings
GROUP BY destination;
"""

# Execute the SQL query
cursor.execute(sql_query)

# print the results
results = cursor.fetchall()
for destination, count in results:
    print(f"Number of people who want to go to {destination}: {count}")

sql_query = "SELECT COUNT(*) FROM flights WHERE destination_city = 'Mumbai';"
cursor.execute(sql_query)
result = cursor.fetchone()[0]
print("Number of flights to Mumbai:", result)

# Close the cursor and connection
cursor.close()
conn.close()

Number of people who want to go to Bangalore: 5
Number of people who want to go to Chennai: 5
Number of people who want to go to Delhi: 5
Number of people who want to go to Hyderabad: 5
Number of people who want to go to Kolkata: 5
Number of people who want to go to Mumbai: 5
Number of flights to Mumbai: 59097


** could not find SQL dataset